# Calculate Urban Metrics: Structure
using this example notebook: https://github.com/gboeing/osmnx-examples/blob/master/notebooks/06-stats-indicators-centrality.ipynb

OSMnx now caches server responses by default. This can be changed with ox.config(use_cache=False). The caching hash algorithm was changed for v1.0, invalidating old caches made with prior releases.

### Import libraries

In [16]:
import logging

import geopandas as gpd
import pandas as pd
import osmnx as ox

In [17]:
logging.basicConfig(filename="urban_structure_metrics.log", level=logging.INFO)

In [18]:
import time

start_time = time.time()

In [19]:
inputFolder = r"input_folder"
# define output folder
outputFolder = r"output_folder"

### You may need to use the 'Fix geometries' tool in QGIS beforehand to fix the geometries

In [20]:
# read extents in WGS84
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\russia_urban_extents_merged_4326.shp"
# shpName = r"C:\repos\GOST_Urban\Notebooks\Implementations\eca_wo_rus_urban_clusters_ghs_pop_smooth_100k_4326_3.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UBZ_only_FUAs2_geom_fixed.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_ghs_built_up_extents_4326\UZB_only_ghs_built_up_extents_4326_geom_fixed_greater_50k.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_ghs_built_up_extents_4326\UZB_only_ghs_built_up_extents_4326_geom_fixed.shp"
# shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\ECA_wo_rus_urban_extents\eca_wo_rus_built_up_extents_4326.shp"
shpName = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\all_urban_clusters_5k_up_4326.shp"

In [21]:
input_shapes_gpd = gpd.read_file(shpName)

In [22]:
input_shapes_gpd

ID            Pop                             layer  \
0     2038    5213.978912                              None   
1     2355    8086.003265                              None   
2     2691   12046.157654                              None   
3     2753   11929.881653                              None   
4     3060  115285.056396                              None   
...    ...            ...                               ...   
7993    32    6807.330750  27_urban_clusters_ghs_pop_russia   
7994    28   20279.139618  27_urban_clusters_ghs_pop_russia   
7995    18    8344.212311  27_urban_clusters_ghs_pop_russia   
7996    15    5386.852844  27_urban_clusters_ghs_pop_russia   
7997    55    5909.184235  26_urban_clusters_ghs_pop_russia   

                                                   path  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
7993  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7994  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7995  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7996  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7997  C:/repos/GOST_Urban/Notebooks/Implementations/...   

                                               geometry  
0     POLYGON ((28.77793 55.91414, 28.82094 55.91414...  
1     POLYGON ((27.94342 55.81376, 27.95774 55.81376...  
2     POLYGON ((27.02823 55.65336, 27.08535 55.65336...  
3     POLYGON ((27.60467 55.63333, 27.64749 55.63333...  
4     POLYGON ((28.66157 55.57325, 28.67583 55.57325...  
...                                                 ...  
7993  POLYGON ((105.12725 54.81515, 105.18361 54.815...  
7994  POLYGON ((109.32656 55.65336, 109.36940 55.653...  
7995  POLYGON ((107.47868 56.19569, 107.49308 56.195...  
7996  POLYGON ((116.09091 56.33675, 116.10535 56.336...  
7997  POLYGON ((129.66321 61.92831, 129.67924 61.928...  

[7998 rows x 5 columns]

In [23]:
# input_shapes_gpd = input_shapes_gpd[137:]

In [24]:
%%time

error_list = []

# for entry in input_shapes_gpd.head(2).iterrows():
for entry in input_shapes_gpd.iterrows():
    try:
        print(entry[0])
        # extract the geometry in GeoJSON format
        geometry = entry[1]["geometry"]  # list of shapely geometries

        gdf = gpd.GeoDataFrame()
        gdf["geometry"] = None
        gdf.loc[0, "geometry"] = geometry
        # Set the GeoDataFrame's coordinate system to WGS84
        gdf.crs = "epsg:4326"
        area = ox.project_gdf(gdf).unary_union.area
        print(area)

        G = ox.graph_from_polygon(geometry)
        # calculate basic and extended network stats, merge them together, and display
        stats = ox.basic_stats(G, area=area)
        print(stats)
        print(f"circuity_avg is: {stats['circuity_avg']}")

        # creates a temporary GDF for just the row's shape
        temp_gdf = input_shapes_gpd.loc[[entry[0]]]

        # print("print temp_gdf")
        # print(temp_gdf)

        # Put all metrics in a DataFrame
        metrics_scalar = {}
        metrics_scalar["circuity_avg"] = [stats["circuity_avg"]]
        metrics_scalar["intersection_density_km"] = [stats["intersection_density_km"]]
        metrics_scalar["street_density_km"] = [stats["street_density_km"]]
        metrics_df = pd.DataFrame(metrics_scalar)

        # print("print metrics_scalar")
        # print(metrics_scalar)

        # and concatinate it with the row's shape
        new_temp_gdf = pd.concat([temp_gdf.reset_index(drop=True), metrics_df], axis=1)

        # print("print new_temp_gdf")
        # print(new_temp_gdf)
        # print(entry[0])
        # put the results of each row into a new DataFrame
        if entry[0] == 0:
            print("new_temp_gdf")
            output_new_temp_gdf = new_temp_gdf
        else:
            output_new_temp_gdf = output_new_temp_gdf.append(
                new_temp_gdf, ignore_index=True
            )
    except:
        print(f"error with entry {entry[0]}")
        error_list.append(entry[0])
        # logging.INFO(f"error with entry {entry[0]}" + "\n" + f"entry information: {entry[1]}")

        # creates a temporary GDF for just the row's shape
        #         temp_gdf = input_shapes_gpd.loc[[entry[0]]]
        # Put all metrics in a DataFrame
        #         metrics_scalar = {}
        #         metrics_scalar['circuity_avg'] = 0
        #         metrics_scalar['intersection_density_km'] = 0
        #         metrics_scalar['street_density_km'] = 0
        #         metrics_df = pd.DataFrame(metrics_scalar)
        # and concatinate it with the row's shape
        #         new_temp_gdf = pd.concat([temp_gdf.reset_index(drop=True), metrics_df], axis=1)
        #         output_new_temp_gdf = output_new_temp_gdf.append(new_temp_gdf, ignore_index=True)
        continue

0
6012008.143118326
{'n': 321, 'm': 825, 'k_avg': 5.140186915887851, 'intersection_count': 249, 'streets_per_node_avg': 2.6791277258566977, 'streets_per_node_counts': {0: 0, 1: 72, 2: 0, 3: 209, 4: 39, 5: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.22429906542056074, 2: 0.0, 3: 0.6510903426791277, 4: 0.12149532710280374, 5: 0.003115264797507788}, 'edge_length_total': 85601.38100000018, 'edge_length_avg': 103.75924969696992, 'street_length_total': 42820.80599999999, 'street_length_avg': 103.68233898305083, 'street_segments_count': 413, 'node_density_km': 53.3931412530494, 'intersection_density_km': 41.41710957012243, 'edge_density_km': 14238.400707754234, 'street_density_km': 7122.546240895404, 'circuity_avg': 1.0864182261903164, 'self_loop_proportion': 0.007272727272727273, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0864182261903164
new_temp_gdf
1
9015697.47160323
{'n': 494, 'm': 1204, 'k_avg': 4.874493927125506, 'intersection_count

{'n': 312, 'm': 742, 'k_avg': 4.756410256410256, 'intersection_count': 210, 'streets_per_node_avg': 2.4358974358974357, 'streets_per_node_counts': {0: 0, 1: 102, 2: 0, 3: 183, 4: 26, 5: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.3269230769230769, 2: 0.0, 3: 0.5865384615384616, 4: 0.08333333333333333, 5: 0.003205128205128205}, 'edge_length_total': 82010.40199999987, 'edge_length_avg': 110.52614824797826, 'street_length_total': 41005.20100000001, 'street_length_avg': 110.52614824797845, 'street_segments_count': 371, 'node_density_km': 44.491819280624405, 'intersection_density_km': 29.946416823497195, 'edge_density_km': 11694.846105497923, 'street_density_km': 5847.423052748973, 'circuity_avg': 1.103418931898739, 'self_loop_proportion': 0.008086253369272238, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.103418931898739
10
110253683.5378424
error with entry 10
11
15023415.38161467
{'n': 879, 'm': 2239, 'k_avg': 5.094425483503982, 'interse

{'n': 667, 'm': 1751, 'k_avg': 5.250374812593703, 'intersection_count': 520, 'streets_per_node_avg': 2.6926536731634183, 'streets_per_node_counts': {0: 0, 1: 147, 2: 0, 3: 432, 4: 87, 5: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.22038980509745126, 2: 0.0, 3: 0.6476761619190404, 4: 0.13043478260869565, 5: 0.0014992503748125937}, 'edge_length_total': 157500.73899999997, 'edge_length_avg': 89.94902284408907, 'street_length_total': 79151.02900000004, 'street_length_avg': 89.94435113636368, 'street_segments_count': 880, 'node_density_km': 66.57461341973926, 'intersection_density_km': 51.90224734372476, 'edge_density_km': 15720.465985379684, 'street_density_km': 7900.223624362179, 'circuity_avg': 1.068651957712084, 'self_loop_proportion': 0.006853226727584237, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.068651957712084
21
11016232.571234627
{'n': 569, 'm': 1574, 'k_avg': 5.532513181019332, 'intersection_count': 476, 'streets_per_node_avg

{'n': 4368, 'm': 12300, 'k_avg': 5.631868131868132, 'intersection_count': 3714, 'streets_per_node_avg': 2.9228479853479854, 'streets_per_node_counts': {0: 0, 1: 654, 2: 4, 3: 2756, 4: 934, 5: 19, 6: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.14972527472527472, 2: 0.0009157509157509158, 3: 0.6309523809523809, 4: 0.21382783882783882, 5: 0.00434981684981685, 6: 0.00022893772893772894}, 'edge_length_total': 709662.5679999996, 'edge_length_avg': 57.69614373983737, 'street_length_total': 361416.04700000165, 'street_length_avg': 57.077707991156295, 'street_segments_count': 6332, 'node_density_km': 174.3425240319263, 'intersection_density_km': 148.23904172494832, 'edge_density_km': 28325.174751854043, 'street_density_km': 14425.408850645968, 'circuity_avg': 1.059306517353225, 'self_loop_proportion': 0.0016260162601626016, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.059306517353225
31
53109474.866279155
{'n': 6171, 'm': 17297, 'k_avg': 5.605

{'n': 1376, 'm': 3718, 'k_avg': 5.40406976744186, 'intersection_count': 1141, 'streets_per_node_avg': 2.82921511627907, 'streets_per_node_counts': {0: 0, 1: 235, 2: 0, 3: 913, 4: 222, 5: 5, 6: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.17078488372093023, 2: 0.0, 3: 0.6635174418604651, 4: 0.1613372093023256, 5: 0.003633720930232558, 6: 0.0007267441860465116}, 'edge_length_total': 312351.20199999964, 'edge_length_avg': 84.01054384077452, 'street_length_total': 158723.35700000048, 'street_length_avg': 83.36310766806749, 'street_segments_count': 1904, 'node_density_km': 98.1424593528143, 'intersection_density_km': 81.38121084415779, 'edge_density_km': 22278.281356168354, 'street_density_km': 11320.85800342644, 'circuity_avg': 1.0776443111524885, 'self_loop_proportion': 0.005917159763313609, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0776443111524885
40
7010018.160093949
{'n': 937, 'm': 2538, 'k_avg': 5.417289220917823, 'intersection_co

...

{'n': 54, 'm': 120, 'k_avg': 4.444444444444445, 'intersection_count': 39, 'streets_per_node_avg': 2.4814814814814814, 'streets_per_node_counts': {0: 0, 1: 15, 2: 0, 3: 37, 4: 2}, 'streets_per_node_proportion': {0: 0.0, 1: 0.2777777777777778, 2: 0.0, 3: 0.6851851851851852, 4: 0.037037037037037035}, 'edge_length_total': 20748.694, 'edge_length_avg': 172.90578333333332, 'street_length_total': 10374.346999999996, 'street_length_avg': 172.90578333333326, 'street_segments_count': 60, 'node_density_km': 9.00696371733342, 'intersection_density_km': 6.50502935140747, 'edge_density_km': 3460.791371112104, 'street_density_km': 1730.3956855560514, 'circuity_avg': 1.0855243293619388, 'self_loop_proportion': 0.016666666666666666, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0855243293619388
7951
5995744.270300931
{'n': 553, 'm': 1294, 'k_avg': 4.679927667269439, 'intersection_count': 361, 'streets_per_node_avg': 2.359855334538879, 'streets_per_node_coun

{'n': 1128, 'm': 3022, 'k_avg': 5.358156028368795, 'intersection_count': 898, 'streets_per_node_avg': 2.74822695035461, 'streets_per_node_counts': {0: 0, 1: 230, 2: 0, 3: 724, 4: 172, 5: 2}, 'streets_per_node_proportion': {0: 0.0, 1: 0.20390070921985815, 2: 0.0, 3: 0.6418439716312057, 4: 0.1524822695035461, 5: 0.0017730496453900709}, 'edge_length_total': 380716.86799999914, 'edge_length_avg': 125.98175645268006, 'street_length_total': 190358.43400000007, 'street_length_avg': 125.98175645268039, 'street_segments_count': 1511, 'node_density_km': 56.34345560452503, 'intersection_density_km': 44.85498504686479, 'edge_density_km': 19016.75882096788, 'street_density_km': 9508.379410483965, 'circuity_avg': 1.0416155745379307, 'self_loop_proportion': 0.0013236267372600927, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0416155745379307
7961
9012053.59693724
{'n': 93, 'm': 242, 'k_avg': 5.204301075268817, 'intersection_count': 72, 'streets_per_node_a

{'n': 207, 'm': 538, 'k_avg': 5.1980676328502415, 'intersection_count': 178, 'streets_per_node_avg': 2.821256038647343, 'streets_per_node_counts': {0: 0, 1: 29, 2: 0, 3: 157, 4: 21}, 'streets_per_node_proportion': {0: 0.0, 1: 0.14009661835748793, 2: 0.0, 3: 0.7584541062801933, 4: 0.10144927536231885}, 'edge_length_total': 68591.33399999992, 'edge_length_avg': 127.4931858736058, 'street_length_total': 34295.667000000016, 'street_length_avg': 127.49318587360601, 'street_segments_count': 269, 'node_density_km': 18.789545936337657, 'intersection_density_km': 16.15719409018407, 'edge_density_km': 6226.087058104721, 'street_density_km': 3113.043529052366, 'circuity_avg': 1.03649350064046, 'self_loop_proportion': 0.0, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.03649350064046
7971
8014668.984181628
{'n': 243, 'm': 673, 'k_avg': 5.539094650205762, 'intersection_count': 227, 'streets_per_node_avg': 2.9794238683127574, 'streets_per_node_counts': {0

{'n': 372, 'm': 934, 'k_avg': 5.021505376344086, 'intersection_count': 295, 'streets_per_node_avg': 2.661290322580645, 'streets_per_node_counts': {0: 0, 1: 77, 2: 0, 3: 268, 4: 26, 5: 1}, 'streets_per_node_proportion': {0: 0.0, 1: 0.20698924731182797, 2: 0.0, 3: 0.7204301075268817, 4: 0.06989247311827956, 5: 0.002688172043010753}, 'edge_length_total': 144264.00399999984, 'edge_length_avg': 154.4582483940041, 'street_length_total': 72132.00200000002, 'street_length_avg': 154.45824839400433, 'street_segments_count': 467, 'node_density_km': 30.962847058526215, 'intersection_density_km': 24.553870651250627, 'edge_density_km': 12007.592182533896, 'street_density_km': 6003.796091266956, 'circuity_avg': 1.0622179110750896, 'self_loop_proportion': 0.010706638115631691, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0622179110750896
7983
8009315.285263084
{'n': 172, 'm': 432, 'k_avg': 5.023255813953488, 'intersection_count': 138, 'streets_per_node_av

{'n': 245, 'm': 643, 'k_avg': 5.248979591836735, 'intersection_count': 199, 'streets_per_node_avg': 2.7755102040816326, 'streets_per_node_counts': {0: 0, 1: 46, 2: 0, 3: 164, 4: 33, 5: 2}, 'streets_per_node_proportion': {0: 0.0, 1: 0.18775510204081633, 2: 0.0, 3: 0.6693877551020408, 4: 0.1346938775510204, 5: 0.00816326530612245}, 'edge_length_total': 108891.27499999997, 'edge_length_avg': 169.3487947122861, 'street_length_total': 54498.72799999999, 'street_length_avg': 169.25070807453412, 'street_segments_count': 322, 'node_density_km': 24.420612862354687, 'intersection_density_km': 19.83551820248401, 'edge_density_km': 10853.843554543675, 'street_density_km': 5432.21362440314, 'circuity_avg': 1.0942673558300497, 'self_loop_proportion': 0.003110419906687403, 'clean_intersection_count': None, 'clean_intersection_density_km': None}
circuity_avg is: 1.0942673558300497
7993
10013573.400736034
{'n': 326, 'm': 863, 'k_avg': 5.294478527607362, 'intersection_count': 270, 'streets_per_node_avg'

In [25]:
error_list

[10,
 48,
 53,
 108,
 183,
 209,
 245,
 268,
 278,
 319,
 349,
 356,
 371,
 388,
 410,
 412,
 433,
 453,
 480,
 484,
 489,
 497,
 562,
 574,
 579,
 619,
 628,
 648,
 679,
 685,
 698,
 704,
 707,
 728,
 786,
 837,
 846,
 860,
 892,
 903,
 906,
 920,
 934,
 955,
 968,
 986,
 988,
 996,
 1011,
 1027,
 1030,
 1077,
 1104,
 1140,
 1161,
 1171,
 1233,
 1277,
 1280,
 1291,
 1309,
 1340,
 1347,
 1364,
 1401,
 1421,
 1426,
 1480,
 1511,
 1601,
 1617,
 1621,
 1690,
 1713,
 1726,
 1743,
 1747,
 1752,
 1755,
 1782,
 1783,
 1848,
 1929,
 1967,
 2022,
 2041,
 2052,
 2080,
 2125,
 2140,
 2149,
 2189,
 2269,
 2284,
 2399,
 2417,
 2423,
 2441,
 2492,
 2494,
 2496,
 2526,
 2564,
 2571,
 2580,
 2585,
 2593,
 2632,
 2635,
 2636,
 2648,
 2650,
 2742,
 2809,
 2830,
 2840,
 2856,
 2863,
 2866,
 2875,
 2882,
 2888,
 2914,
 2923,
 2926,
 2944,
 2964,
 3047,
 3059,
 3060,
 3066,
 3067,
 3077,
 3083,
 3085,
 3089,
 3103,
 3123,
 3151,
 3173,
 3175,
 3179,
 3221,
 3223,
 3226,
 3243,
 3252,
 3292,
 3294,
 3307,
 

In [26]:
len(error_list)

694

In [27]:
output_new_temp_gdf

ID            Pop                             layer  \
0     2038    5213.978912                              None   
1     2355    8086.003265                              None   
2     2691   12046.157654                              None   
3     2753   11929.881653                              None   
4     3060  115285.056396                              None   
...    ...            ...                               ...   
7299    32    6807.330750  27_urban_clusters_ghs_pop_russia   
7300    28   20279.139618  27_urban_clusters_ghs_pop_russia   
7301    18    8344.212311  27_urban_clusters_ghs_pop_russia   
7302    15    5386.852844  27_urban_clusters_ghs_pop_russia   
7303    55    5909.184235  26_urban_clusters_ghs_pop_russia   

                                                   path  \
0                                                  None   
1                                                  None   
2                                                  None   
3                                                  None   
4                                                  None   
...                                                 ...   
7299  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7300  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7301  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7302  C:/repos/GOST_Urban/Notebooks/Implementations/...   
7303  C:/repos/GOST_Urban/Notebooks/Implementations/...   

                                               geometry  circuity_avg  \
0     POLYGON ((28.77793 55.91414, 28.82094 55.91414...      1.086418   
1     POLYGON ((27.94342 55.81376, 27.95774 55.81376...      1.080809   
2     POLYGON ((27.02823 55.65336, 27.08535 55.65336...      1.060202   
3     POLYGON ((27.60467 55.63333, 27.64749 55.63333...      1.087695   
4     POLYGON ((28.66157 55.57325, 28.67583 55.57325...      1.075947   
...                                                 ...           ...   
7299  POLYGON ((105.12725 54.81515, 105.18361 54.815...      1.042431   
7300  POLYGON ((109.32656 55.65336, 109.36940 55.653...      1.081767   
7301  POLYGON ((107.47868 56.19569, 107.49308 56.195...      1.071524   
7302  POLYGON ((116.09091 56.33675, 116.10535 56.336...      1.020286   
7303  POLYGON ((129.66321 61.92831, 129.67924 61.928...      1.042990   

      intersection_density_km  street_density_km  
0                   41.417110        7122.546241  
1                   39.043014        7523.374671  
2                   76.072291        9604.515649  
3                   65.888390        9320.870690  
4                  110.619161       11596.405008  
...                       ...                ...  
7299                26.963401        6002.184494  
7300               104.549966       12409.865596  
7301                33.479710        6396.074944  
7302                 6.986790        1837.899113  
7303                18.085843        4946.594377  

[7304 rows x 8 columns]

In [28]:
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_metrics_results_russia"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_urban_metrics_results_wo_rus"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_FUAs_results"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_urban_extents_results"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\UZB_only_GHS_urban_extents_results_all"
# output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\eca_urban_metrics_results_wo_rus_all"
output = r"C:\Users\war-machine\Documents\world_bank_work\UZB_project\metrics_shape_tool\all_urban_extents_results_5k_up"

In [29]:
# save as CSV
# output_new_temp_gdf.to_csv(output + r"\ECA_russia_urban_metrics_100k_structure_to_146.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_FUAs_structure.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_urban_extents_structure.csv")
# output_new_temp_gdf.to_csv(output + r"\UZB_only_urban_metrics_urban_extents_all_structure.csv")
# output_new_temp_gdf.to_csv(output + r"\ECA_wo_rus_urban_metrics_urban_extents_all_structure.csv")
output_new_temp_gdf.to_csv(output + r"\all_urban_metrics_5k_up_structure.csv")

In [30]:
print(f"total time to process: {time.time()-start_time}")

total time to process: 21725.62296462059
